In [ ]:
import requests
import base64
import pandas as pd
from typing import Dict, Any
from dotenv import load_dotenv
load_dotenv()
import os
import json

In [2]:
client_id = os.getenv("SPOTIFY_CLIENT_ID")
client_secret = os.getenv("SPOTIFY_CLIENT_SECRET")

string = client_id + ":" + client_secret
string_bytes = string.encode('ascii')

base64_bytes = base64.b64encode(string_bytes)
base64_string = base64_bytes.decode('ascii')
url = 'https://accounts.spotify.com/api/token'

headers = {
    'Authorization': f'Basic {base64_string}',
    'Content-Type': 'application/x-www-form-urlencoded'
}

payload = {'grant_type': 'client_credentials'}

response = requests.request('POST', url = url, headers = headers, data = payload)
access_token = response.json()['access_token']

In [8]:
def folder_to_df_merged(folder_path: str) -> Dict[str, pd.DataFrame]:
    result = {}

    for file in os.listdir(folder_path):
        if not file.endswith(".json"):
            continue

        path = os.path.join(folder_path, file)

        with open(path, encoding="utf-8") as f:
            data: Any = json.load(f)

        if isinstance(data, list) and all(isinstance(i, dict) for i in data):
            df = pd.json_normalize(data)

        elif isinstance(data, dict):
            list_keys = [k for k, v in data.items() if isinstance(v, list)]

            if list_keys:
                main_key = list_keys[0]
                df = pd.json_normalize(
                    data,
                    record_path=main_key,
                    meta=[k for k in data.keys() if k != main_key],
                    errors="ignore"
                )
            else:
                df = pd.DataFrame([data])

        else:
            df = pd.DataFrame()

        result[file.replace(".json", "")] = df
    
    return pd.concat(result.values(), ignore_index=True)

df = folder_to_df_merged("../data/raw")


In [16]:
df["track_id"] = df["spotify_track_uri"].map(lambda x: str(x).split(":")[2] if len(str(x).split(":")) == 3 else None)
df = df.drop(columns=["spotify_track_uri","platform", "conn_country", "ip_addr", "episode_name", "audiobook_chapter_uri", "audiobook_chapter_title", "episode_show_name", "spotify_episode_uri", "audiobook_title", "audiobook_uri"])


In [18]:
df = df.dropna()

In [20]:
import sqlite3
import json

db_path = "./dados.db"

def json_para_sqlite(table_name, json_data):
    """
    Cria uma tabela SQLite baseada na estrutura do primeiro item de um JSON.
    """
    # Conecta (ou cria) o banco de dados
    conn = sqlite3.connect(db_path)
    cursor = conn.cursor()

    # Pega as chaves (colunas) do primeiro item
    if not json_data:
        print("JSON vazio!")
        return
    
    colunas = list(json_data[0].keys())
    colunas_sql = ", ".join([f"{col} TEXT" for col in colunas]) # Define tudo como TEXT por padrão
    try:
        # 1. Cria a tabela (IF NOT EXISTS)
        create_table_sql = f"CREATE TABLE IF NOT EXISTS {table_name} ({colunas_sql});"
        cursor.execute(create_table_sql)
    

        # 2. Insere os dados
        insert_sql = f"INSERT INTO {table_name} ({', '.join(colunas)}) VALUES ({', '.join(['?' for _ in colunas])});"
        
        for item in json_data:
            valores = [str(item.get(col, "")) for col in colunas]
            cursor.execute(insert_sql, valores)
    except Exception as e:
        print(e)

    conn.commit()
    conn.close()



In [21]:
def get_artist(track_id):
    track_url = f"https://api.spotify.com/v1/tracks/{track_id}"

    track_headers = {'Authorization': f'Bearer {access_token}'}

    track_response = requests.request('GET', url = track_url, headers = track_headers)

    data = track_response.json()

    data = {
        key: data["artists"][0][key] for key in ["id", "name"] if "artists" in data and len(data["artists"]) > 0 and all(key in data["artists"][0] for key in ("id", "name"))
    }
    
    if str(data).lower != 'nan':
        json_para_sqlite("artist", [data])
    return data["id"] if "id" in data else None


In [ ]:
tracks = df["track_id"]

array(['4h8VwCb1MTGoLKueQ1WgbD', '1XGmzt0PVuFgQYYnV2It7A',
       '5oI9blwsXC8AkTWw6wASY8', ..., '4xxRtQEtC5RTaQrpORR4BR',
       '34bIdnuPSyDuDz1uTH8ZiL', '3Ea26wxASNOsuOB4pSRMZp'],
      shape=(7269,), dtype=object)

In [ ]:
track_artist = {}
for x in tracks.unique():
    print(x)
    track_artist[x] = get_artist(x)


3M6auAoAoVyPGxNxe1jcXw
0BCPKOYdS2jbQ8iyB56Zns
4pbJqGIASGPr0ZpGpnWkDn
7snQQk1zcKl8gZ92AnueZW
0HqZX76SFLDz2aW8aiqi7G
5qaEfEh1AtSdrdrByCP7qR
6nPnhrEbkvDvXj9mjGAflk
0pqnGHJpmpxLKifKRmU6WP
7BOFPHYn3P6KiDZfPy9np5
57bgtoPSgt236HzfBOd8kj
10C3nAydzBvNfaY86NwUuA
42et6fnHCw1HIPSrdPprMl
7qiZfU4dY1lWllzX7mPBI3
2SiXAy7TuUkycRVbbWDEpo
2zYzyRzz6pRmhPzyfMEC8s
7mZZZ7uLhi8df4xinKOu0Q
3DwQ7AH3xGD9h65ezslm6q
2LawezPeJhN4AWuSB0GtAU
31L9yLXSj6LpCFupyMV6CR
2Pr6qNmiOxTdo8B6bs8x8x
6Pgkp4qUoTmJIPn7ReaGxL
1xsYj84j7hUDDnTTerGWlH
3nI0piSOxAik2RCpHGloB7
4d0DpU7Odiv0ztvX2GxJlk
2RsAajgo0g7bMCHxwH3Sk0
2JzZzZUQj3Qff7wapcbKjc
6nek1Nin9q48AVZcWs9e9D
4RLp0EpcPdMHHoHmYIMWGH
1fAeFPXsX08Ovnn9iV1x27
0AsfpL8bzbmEyJsfbPPYnj
2Iug43iQrHN8CbGsUd2tEt
5PozhmwZXtIEsaWFwRzYFV
6ttKOudrrD5yjt4saUjhNa
3M3BpvBpECKlcjjxRHzpaB
0y1QJc3SJVPKJ1OvFmFqe6
0C71ubP3YGLAwOgUlbY3d0
006pMMCuRo2TFjh8sNGSov
5kqIPrATaCc2LqxVWzQGbk
5RKQ5NdjSh2QzD4MaunT91
7vM3wi9leaynP5Bmi93VDh
50nfwKoDiSYg8zOCREWAm5
6PwjJ58I4t7Mae9xfZ9l9v
4CeeEOM32jQcH3eN9Q2dGj
3ZOEytgrvLw

In [ ]:
conn = sqlite3.connect(db_path)
cursor = conn.cursor()
cursor.execute('''
DELETE FROM artist
WHERE rowid NOT IN (
    SELECT MIN(rowid)
    FROM artist
    GROUP BY id, name
);
''')
conn.commit()
cursor.close()
conn.close()

In [ ]:
len(list(set(list(track_artist.values()))))

230

In [ ]:
df["artist_id"] = df["track_id"].map(lambda x: track_artist[x])
json_para_sqlite("music_history", df.to_dict(orient="records"))

[{'ts': '2025-06-15T16:07:01Z', 'ms_played': 244760, 'master_metadata_track_name': 'Só Pra Vadiar', 'master_metadata_album_artist_name': 'Charlie Brown Jr.', 'master_metadata_album_album_name': 'Camisa 10 joga bola até na chuva', 'reason_start': 'trackdone', 'reason_end': 'trackdone', 'shuffle': True, 'skipped': False, 'offline': False, 'offline_timestamp': 1750003290, 'incognito_mode': False, 'track_id': '3M6auAoAoVyPGxNxe1jcXw', 'artist_id': '1on7ZQ2pvgeQF4vmIA09x5'}, {'ts': '2025-06-15T16:07:08Z', 'ms_played': 4874, 'master_metadata_track_name': 'Clocks', 'master_metadata_album_artist_name': 'Coldplay', 'master_metadata_album_album_name': 'A Rush of Blood to the Head', 'reason_start': 'trackdone', 'reason_end': 'fwdbtn', 'shuffle': True, 'skipped': True, 'offline': False, 'offline_timestamp': 1750003621, 'incognito_mode': False, 'track_id': '0BCPKOYdS2jbQ8iyB56Zns', 'artist_id': '4gzpq5DPGxSnKTe4SA8HAU'}, {'ts': '2025-06-15T16:07:10Z', 'ms_played': 1620, 'master_metadata_track_name'

In [ ]:
def get_genres(artist_id):
    artist_url = f"https://api.spotify.com/v1/artists/{artist_id}"

    artist_headers = {'Authorization': f'Bearer {access_token}'}

    response = requests.request('GET', url = artist_url, headers = artist_headers)

    data = response.json()

    genres = data["genres"]
    
    data = list(map((lambda x: {"artist_id": artist_id, "genre": x}), genres))



    json_para_sqlite("artist_genre", data)
    return genres

In [ ]:
artists = df["artist_id"]
artists.unique()

<StringArray>
['1on7ZQ2pvgeQF4vmIA09x5', '4gzpq5DPGxSnKTe4SA8HAU', '1dfeR4HaWDbWqFHLkxsg1d',
 '3qm84nBOXUEQ2vnTfUTTFC', '53XhwfbYqKCa1cC15pYq2q', '6tw6EpC9RgmSRZiZg0n22t',
 '632WMoQfBWk76kBz7vMXNg', '711MCceyCBcFnzjGY4Q7Un', '1PwOU6fFbmaGkK3wkbb8fU',
 '6TcnmlCSxihzWOQJ8k0rNS',
 ...
 '1w5Kfo2jwwIPruYS2UWh56', '2cGwlqi3k18jFpUyTrsR84', '22bE4uQ6baNwSHPVcDxLCe',
 '0Je74SitssvJg1w4Ra2EK7', '568ZhdwyaiCyOGJRtNYhWf', '6IRouO5mvvfcyxtPDKMYFN',
 '2AM4ilv6UzW0uMRuqKtDgN', '3ICflSq6ZgYAIrm2CTkfVP', '52xstrfqEahsQREdysdsgr',
 '2XlHqPf6rMXNqdd5LTpFhE']
Length: 229, dtype: str

In [ ]:
artist_genre = {}
for x in artists.unique():
    artist_genre[x] = get_genres(x)


[{'artist_id': '1on7ZQ2pvgeQF4vmIA09x5', 'genre': 'brazilian rock'}, {'artist_id': '1on7ZQ2pvgeQF4vmIA09x5', 'genre': 'mpb'}, {'artist_id': '1on7ZQ2pvgeQF4vmIA09x5', 'genre': 'brazilian pop'}]
[]
JSON vazio!
[{'artist_id': '1dfeR4HaWDbWqFHLkxsg1d', 'genre': 'classic rock'}, {'artist_id': '1dfeR4HaWDbWqFHLkxsg1d', 'genre': 'rock'}, {'artist_id': '1dfeR4HaWDbWqFHLkxsg1d', 'genre': 'glam rock'}]
[{'artist_id': '3qm84nBOXUEQ2vnTfUTTFC', 'genre': 'rock'}, {'artist_id': '3qm84nBOXUEQ2vnTfUTTFC', 'genre': 'glam metal'}, {'artist_id': '3qm84nBOXUEQ2vnTfUTTFC', 'genre': 'hard rock'}, {'artist_id': '3qm84nBOXUEQ2vnTfUTTFC', 'genre': 'classic rock'}]
[]
JSON vazio!
[{'artist_id': '6tw6EpC9RgmSRZiZg0n22t', 'genre': 'brazilian rock'}, {'artist_id': '6tw6EpC9RgmSRZiZg0n22t', 'genre': 'mpb'}, {'artist_id': '6tw6EpC9RgmSRZiZg0n22t', 'genre': 'brazilian pop'}]
[]
JSON vazio!
[{'artist_id': '711MCceyCBcFnzjGY4Q7Un', 'genre': 'rock'}, {'artist_id': '711MCceyCBcFnzjGY4Q7Un', 'genre': 'hard rock'}, {'artis

In [ ]:
artist_genre

{'1on7ZQ2pvgeQF4vmIA09x5': ['brazilian rock', 'mpb', 'brazilian pop'],
 '4gzpq5DPGxSnKTe4SA8HAU': [],
 '1dfeR4HaWDbWqFHLkxsg1d': ['classic rock', 'rock', 'glam rock'],
 '3qm84nBOXUEQ2vnTfUTTFC': ['rock', 'glam metal', 'hard rock', 'classic rock'],
 '53XhwfbYqKCa1cC15pYq2q': [],
 '6tw6EpC9RgmSRZiZg0n22t': ['brazilian rock', 'mpb', 'brazilian pop'],
 '632WMoQfBWk76kBz7vMXNg': [],
 '711MCceyCBcFnzjGY4Q7Un': ['rock',
  'hard rock',
  'classic rock',
  'rock and roll'],
 '1PwOU6fFbmaGkK3wkbb8fU': ['mpb', 'brazilian rock', 'brazilian pop'],
 '6TcnmlCSxihzWOQJ8k0rNS': [],
 '6eUKZXaKkcviH0Ku9w2n3V': ['soft pop'],
 '2A9ZOE4ukWNyIjDhtUyp45': ['brazilian rock', 'mpb', 'brazilian pop'],
 '2ye2Wgw4gimLv2eAKyk1NB': ['metal',
  'thrash metal',
  'rock',
  'heavy metal',
  'hard rock'],
 '3IYUhFvPQItj6xySrBmZkd': ['classic rock', 'southern rock', 'country rock'],
 '1vCWHaC5f2uS3yhpwWbIA6': ['edm'],
 '7Ey4PD4MYsKc5I2dolUwbH': ['classic rock', 'rock'],
 '6olE6TJLqED3rqDCT0FyPh': ['grunge', 'rock'],
 '13